In [1]:
from pathlib import Path

import numpy as np
import pandas as pd
from sklearn.preprocessing import FunctionTransformer
from sklearn.preprocessing import OneHotEncoder
from sklearn.preprocessing import StandardScaler
from sklearn.pipeline import make_pipeline
from sklearn.compose import ColumnTransformer
from sklearn.linear_model import Ridge
from sklearn.ensemble import RandomForestRegressor
import xgboost as xgb
from xgboost.sklearn import XGBRegressor
from sklearn.ensemble import BaggingRegressor, RandomForestRegressor, AdaBoostRegressor
from sklearn.svm import SVR
import lightgbm as lgb
from sklearn.neighbors import KNeighborsRegressor

In [2]:
import pickle
from urllib.request import urlopen
from pathlib import Path
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt

np.random.seed(42)
np.random.RandomState(42)

import seaborn as sns

#import unittest
from nose.tools import *

import time
import datetime as dt
import statsmodels.api as sm
from scipy import stats
from scipy.stats import norm, skew, kurtosis

from sklearn.linear_model import LinearRegression
from sklearn.svm import SVR
from sklearn.model_selection import train_test_split, TimeSeriesSplit, GridSearchCV,cross_val_score 
from sklearn import preprocessing
from sklearn.ensemble import BaggingRegressor, RandomForestRegressor, AdaBoostRegressor
from xgboost.sklearn import XGBRegressor
from sklearn.metrics import mean_absolute_error,r2_score, mean_squared_log_error,mean_squared_error, make_scorer

from sklearn.compose import ColumnTransformer
from sklearn.linear_model import Ridge
from sklearn.pipeline import make_pipeline
from sklearn.preprocessing import FunctionTransformer
from sklearn.preprocessing import OneHotEncoder
from sklearn.model_selection import RandomizedSearchCV
import joblib
from catboost import CatBoostRegressor
from sklearn.ensemble import GradientBoostingRegressor
from lightgbm import LGBMRegressor

In [3]:
fin_ext_data = pd.read_csv("/Users/madhuranirale/Desktop/Project/Python_DS_Project/external_data_no_cyc.csv")

In [4]:
data = pd.read_parquet(Path("data") / "train.parquet")

In [5]:
data1 = pd.read_parquet(Path("data") / "test.parquet")

In [6]:
fin_ext_data

Unnamed: 0                 date  temp  dwpt  rhum  prcp   wdir  wspd  \
0               0  2020-01-01 00:00:00   0.8  -0.1    94   0.0  170.0   5.4   
1               1  2020-01-01 01:00:00  -0.7  -1.3    96   0.0  200.0   9.4   
2               2  2020-01-01 02:00:00  -0.3  -0.6    98   0.0  190.0   7.6   
3               3  2020-01-01 03:00:00   0.0  -0.3    98   0.0  220.0   5.4   
4               4  2020-01-01 04:00:00   0.3   0.0    98   0.0  210.0   7.6   
...           ...                  ...   ...   ...   ...   ...    ...   ...   
17411       17411  2021-12-31 19:00:00  11.9  10.3    90   0.0  250.0   5.4   
17412       17412  2021-12-31 20:00:00  12.0  10.6    91   0.0  280.0  11.2   
17413       17413  2021-12-31 21:00:00  12.2  10.9    92   0.0  280.0   7.6   
17414       17414  2021-12-31 22:00:00  12.0  10.6    91   0.0  270.0   3.6   
17415       17415  2021-12-31 23:00:00  11.8  10.5    92   0.0  190.0   9.4   

         pres  holiday  weekend  lockdown1  lockdown2  season  is_night  
0      1032.5        1        0          0          0       3         1  
1      1032.2        1        0          0          0       3         1  
2      1032.2        1        0          0          0       3         1  
3      1031.9        1        0          0          0       3         1  
4      1031.6        1        0          0          0       3         1  
...       ...      ...      ...        ...        ...     ...       ...  
17411  1026.5        0        0          0          0       3         0  
17412  1026.6        0        0          0          0       3         1  
17413  1026.6        0        0          0          0       3         1  
17414  1026.7        0        0          0          0       3         1  
17415  1026.6        0        0          0          0       3         1  

[17416 rows x 15 columns]

In [7]:
fin_ext_data = fin_ext_data.drop(['Unnamed: 0'], axis=1)
fin_ext_data['date'] = pd.to_datetime(fin_ext_data['date'])

In [8]:
train_merged = data.merge(fin_ext_data, on='date')

In [9]:
test_merged = data1.merge(fin_ext_data, on='date')

In [10]:
data_tr = train_merged.sort_values(["date", "counter_name"])
y_train = data_tr["log_bike_count"].values
X_train = data_tr.drop(["log_bike_count", "bike_count"], axis=1)

In [11]:
data_ts = test_merged.sort_values(["date", "counter_name"])
y_test = data_ts["log_bike_count"].values
X_test = data_ts.drop(["log_bike_count", "bike_count"], axis=1)

In [12]:
def _encode_dates(X):
    X = X.copy()  # modify a copy of X
    X.loc[:, "year"] = X["date"].dt.year
    X.loc[:, "month"] = X["date"].dt.month
    X.loc[:, "day"] = X["date"].dt.day
    X.loc[:, "weekday"] = X["date"].dt.weekday
    X.loc[:, "hour"] = X["date"].dt.hour

    # Finally we can drop the original columns from the dataframe
    return X.drop(columns=["date"])

In [13]:
from sklearn.compose import ColumnTransformer
from sklearn.linear_model import Ridge
from sklearn.pipeline import make_pipeline
import time

date_encoder = FunctionTransformer(_encode_dates)
date_cols = _encode_dates(X_train[["date"]]).columns.tolist()
num_features = ['temp', 'dwpt', 'rhum', 'prcp', 'wdir', 'wspd', 'pres']

categorical_encoder = OneHotEncoder(handle_unknown="ignore")
categorical_cols = ["counter_name", "site_name", "season"]

rest_cols = ['holiday', 'weekend', 'is_night', 'lockdown1', 'lockdown2']

preprocessor = ColumnTransformer(
    [
        ("date", OneHotEncoder(handle_unknown="ignore"), date_cols),
        ("cat", categorical_encoder, categorical_cols),
        ("numf", StandardScaler(), num_features),
        ("rem", 'passthrough', rest_cols)
    ]
)

params = {
 "catboostregressor__iterations" : [100, 300, 500, 700, 1000],
 "catboostregressor__max_depth" : [6, 8, 10],
 "catboostregressor__l2_leaf_reg" : [4, 5, 6, 7, 8, 9, 10],
 "catboostregressor__learning_rate": [0.03, 0.05, 0.07, 0.1],
 "catboostregressor__bagging_temperature" : [ 0.3, 0.4, 0.5 , 0.7],
 "catboostregressor__random_strength" : [3, 4, 5, 6]
}

regressor = CatBoostRegressor()
pipe = make_pipeline(date_encoder, preprocessor, regressor)
rscv = RandomizedSearchCV(pipe, param_distributions=params, n_iter=50, scoring="neg_root_mean_squared_error", n_jobs=-1, cv=5, verbose=3)
rscv.fit(X_train, y_train)

Fitting 5 folds for each of 50 candidates, totalling 250 fits
0:	learn: 1.6103706	total: 282ms	remaining: 1m 24s
1:	learn: 1.5658515	total: 401ms	remaining: 59.7s
2:	learn: 1.5249605	total: 496ms	remaining: 49.1s
3:	learn: 1.4856863	total: 650ms	remaining: 48.1s
4:	learn: 1.4496453	total: 735ms	remaining: 43.4s
5:	learn: 1.4162041	total: 818ms	remaining: 40.1s
6:	learn: 1.3841679	total: 894ms	remaining: 37.4s
7:	learn: 1.3559357	total: 1.1s	remaining: 40s
8:	learn: 1.3296034	total: 1.22s	remaining: 39.3s
9:	learn: 1.3028603	total: 1.4s	remaining: 40.7s
10:	learn: 1.2788472	total: 1.49s	remaining: 39.2s
11:	learn: 1.2571938	total: 1.56s	remaining: 37.5s
12:	learn: 1.2348097	total: 1.64s	remaining: 36.3s
13:	learn: 1.2150502	total: 1.77s	remaining: 36.2s
14:	learn: 1.1973113	total: 1.98s	remaining: 37.6s
15:	learn: 1.1798763	total: 2.16s	remaining: 38.3s
16:	learn: 1.1643795	total: 2.25s	remaining: 37.4s
17:	learn: 1.1499120	total: 2.41s	remaining: 37.7s
18:	learn: 1.1361519	total: 2.5s	

6:	learn: 1.3891261	total: 1.95s	remaining: 1m 21s
7:	learn: 1.3596257	total: 2.19s	remaining: 1m 20s
8:	learn: 1.3308738	total: 2.72s	remaining: 1m 27s
9:	learn: 1.3042778	total: 3s	remaining: 1m 26s
10:	learn: 1.2801867	total: 3.21s	remaining: 1m 24s
11:	learn: 1.2556966	total: 3.55s	remaining: 1m 25s
12:	learn: 1.2334781	total: 3.81s	remaining: 1m 24s
0:	learn: 1.6284271	total: 389ms	remaining: 1m 56s
1:	learn: 1.5819116	total: 619ms	remaining: 1m 32s
2:	learn: 1.5406502	total: 856ms	remaining: 1m 24s
3:	learn: 1.5010330	total: 1.15s	remaining: 1m 24s
4:	learn: 1.4647552	total: 1.25s	remaining: 1m 13s
5:	learn: 1.4308928	total: 1.42s	remaining: 1m 9s
6:	learn: 1.3975346	total: 1.6s	remaining: 1m 7s
7:	learn: 1.3692601	total: 1.83s	remaining: 1m 6s
8:	learn: 1.3432739	total: 2.15s	remaining: 1m 9s
9:	learn: 1.3167108	total: 2.39s	remaining: 1m 9s
10:	learn: 1.2927657	total: 2.47s	remaining: 1m 4s
11:	learn: 1.2704631	total: 2.77s	remaining: 1m 6s
12:	learn: 1.2489279	total: 2.98s	rem

0:	learn: 1.6252984	total: 233ms	remaining: 1m 9s
1:	learn: 1.5787628	total: 475ms	remaining: 1m 10s
2:	learn: 1.5345190	total: 738ms	remaining: 1m 13s
3:	learn: 1.4950342	total: 1.01s	remaining: 1m 14s
4:	learn: 1.4568096	total: 1.2s	remaining: 1m 11s
5:	learn: 1.4243732	total: 1.36s	remaining: 1m 6s
6:	learn: 1.3901212	total: 1.63s	remaining: 1m 8s
7:	learn: 1.3574023	total: 1.75s	remaining: 1m 3s
8:	learn: 1.3267426	total: 2.04s	remaining: 1m 5s
9:	learn: 1.2995061	total: 2.12s	remaining: 1m 1s
10:	learn: 1.2726855	total: 2.36s	remaining: 1m 1s
11:	learn: 1.2495296	total: 2.56s	remaining: 1m 1s
12:	learn: 1.2278793	total: 2.86s	remaining: 1m 3s
13:	learn: 1.2070568	total: 3.22s	remaining: 1m 5s
14:	learn: 1.1859928	total: 3.5s	remaining: 1m 6s
15:	learn: 1.1676665	total: 3.67s	remaining: 1m 5s
16:	learn: 1.1512972	total: 3.79s	remaining: 1m 3s
17:	learn: 1.1355118	total: 3.96s	remaining: 1m 1s
18:	learn: 1.1190338	total: 4.2s	remaining: 1m 2s
19:	learn: 1.1052322	total: 4.31s	remain

13:	learn: 1.2130888	total: 4.05s	remaining: 1m 22s
14:	learn: 1.1937133	total: 4.13s	remaining: 1m 18s
15:	learn: 1.1760025	total: 4.42s	remaining: 1m 18s
16:	learn: 1.1603989	total: 4.66s	remaining: 1m 17s
17:	learn: 1.1454159	total: 4.94s	remaining: 1m 17s
18:	learn: 1.1308522	total: 5.21s	remaining: 1m 17s
19:	learn: 1.1165635	total: 5.54s	remaining: 1m 17s
20:	learn: 1.1029147	total: 5.69s	remaining: 1m 15s
21:	learn: 1.0903327	total: 5.9s	remaining: 1m 14s
22:	learn: 1.0799626	total: 6.02s	remaining: 1m 12s
23:	learn: 1.0690730	total: 6.54s	remaining: 1m 15s
24:	learn: 1.0580178	total: 6.75s	remaining: 1m 14s
25:	learn: 1.0488693	total: 7.21s	remaining: 1m 16s
26:	learn: 1.0386399	total: 7.42s	remaining: 1m 15s
27:	learn: 1.0307779	total: 7.56s	remaining: 1m 13s
28:	learn: 1.0227641	total: 7.91s	remaining: 1m 13s
29:	learn: 1.0150787	total: 8.12s	remaining: 1m 13s
30:	learn: 1.0072810	total: 8.43s	remaining: 1m 13s
31:	learn: 1.0000646	total: 8.83s	remaining: 1m 13s
32:	learn: 0.

14:	learn: 1.1938056	total: 2.11s	remaining: 40.2s
15:	learn: 1.1736614	total: 2.28s	remaining: 40.5s
16:	learn: 1.1562541	total: 2.33s	remaining: 38.8s
17:	learn: 1.1386012	total: 2.38s	remaining: 37.3s
18:	learn: 1.1221690	total: 2.64s	remaining: 39.1s
19:	learn: 1.1079238	total: 2.74s	remaining: 38.3s
20:	learn: 1.0935054	total: 2.85s	remaining: 37.8s
21:	learn: 1.0816210	total: 2.94s	remaining: 37.2s
22:	learn: 1.0697625	total: 3.17s	remaining: 38.2s
23:	learn: 1.0591053	total: 3.26s	remaining: 37.5s
24:	learn: 1.0487835	total: 3.33s	remaining: 36.6s
25:	learn: 1.0398703	total: 3.49s	remaining: 36.8s
26:	learn: 1.0307823	total: 3.68s	remaining: 37.2s
27:	learn: 1.0228638	total: 3.79s	remaining: 36.9s
28:	learn: 1.0145549	total: 3.87s	remaining: 36.2s
29:	learn: 1.0078895	total: 4.09s	remaining: 36.8s
30:	learn: 1.0011476	total: 4.2s	remaining: 36.5s
31:	learn: 0.9943770	total: 4.42s	remaining: 37s
32:	learn: 0.9881324	total: 4.51s	remaining: 36.5s
33:	learn: 0.9825486	total: 4.66s	

...

472:	learn: 0.4504425	total: 1m 16s	remaining: 1m 24s
473:	learn: 0.4500946	total: 1m 16s	remaining: 1m 24s
474:	learn: 0.4498228	total: 1m 16s	remaining: 1m 24s
475:	learn: 0.4496674	total: 1m 16s	remaining: 1m 24s
476:	learn: 0.4493788	total: 1m 16s	remaining: 1m 24s
477:	learn: 0.4491896	total: 1m 16s	remaining: 1m 24s
478:	learn: 0.4490399	total: 1m 17s	remaining: 1m 23s
479:	learn: 0.4488734	total: 1m 17s	remaining: 1m 23s
480:	learn: 0.4486566	total: 1m 17s	remaining: 1m 23s
481:	learn: 0.4485080	total: 1m 17s	remaining: 1m 23s
482:	learn: 0.4483380	total: 1m 17s	remaining: 1m 23s
483:	learn: 0.4481247	total: 1m 17s	remaining: 1m 22s
484:	learn: 0.4479784	total: 1m 17s	remaining: 1m 22s
485:	learn: 0.4478365	total: 1m 18s	remaining: 1m 22s
486:	learn: 0.4476500	total: 1m 18s	remaining: 1m 22s
487:	learn: 0.4475045	total: 1m 18s	remaining: 1m 22s
488:	learn: 0.4473233	total: 1m 18s	remaining: 1m 22s
489:	learn: 0.4471451	total: 1m 18s	remaining: 1m 21s
490:	learn: 0.4470007	total:

627:	learn: 0.4260052	total: 1m 41s	remaining: 59.9s
628:	learn: 0.4257585	total: 1m 41s	remaining: 59.8s
629:	learn: 0.4255764	total: 1m 41s	remaining: 59.6s
630:	learn: 0.4254053	total: 1m 41s	remaining: 59.4s
631:	learn: 0.4252642	total: 1m 41s	remaining: 59.3s
632:	learn: 0.4251533	total: 1m 41s	remaining: 59.1s
633:	learn: 0.4249849	total: 1m 42s	remaining: 58.9s
634:	learn: 0.4248564	total: 1m 42s	remaining: 58.7s
635:	learn: 0.4247233	total: 1m 42s	remaining: 58.6s
636:	learn: 0.4246643	total: 1m 42s	remaining: 58.4s
637:	learn: 0.4245283	total: 1m 42s	remaining: 58.3s
638:	learn: 0.4244153	total: 1m 42s	remaining: 58.2s
639:	learn: 0.4243166	total: 1m 43s	remaining: 58s
640:	learn: 0.4241204	total: 1m 43s	remaining: 57.8s
641:	learn: 0.4240351	total: 1m 43s	remaining: 57.6s
642:	learn: 0.4239485	total: 1m 43s	remaining: 57.4s
643:	learn: 0.4238193	total: 1m 43s	remaining: 57.2s
644:	learn: 0.4237060	total: 1m 43s	remaining: 57.1s
645:	learn: 0.4235911	total: 1m 43s	remaining: 5

785:	learn: 0.4074348	total: 2m 7s	remaining: 34.8s
786:	learn: 0.4073523	total: 2m 8s	remaining: 34.7s
787:	learn: 0.4072732	total: 2m 8s	remaining: 34.5s
788:	learn: 0.4071358	total: 2m 8s	remaining: 34.4s
789:	learn: 0.4070481	total: 2m 8s	remaining: 34.2s
790:	learn: 0.4069361	total: 2m 8s	remaining: 34s
791:	learn: 0.4068684	total: 2m 8s	remaining: 33.9s
792:	learn: 0.4067970	total: 2m 9s	remaining: 33.7s
793:	learn: 0.4066462	total: 2m 9s	remaining: 33.5s
794:	learn: 0.4065388	total: 2m 9s	remaining: 33.4s
795:	learn: 0.4064576	total: 2m 9s	remaining: 33.2s
796:	learn: 0.4063679	total: 2m 9s	remaining: 33.1s
797:	learn: 0.4062713	total: 2m 9s	remaining: 32.9s
798:	learn: 0.4062002	total: 2m 10s	remaining: 32.7s
799:	learn: 0.4061004	total: 2m 10s	remaining: 32.6s
800:	learn: 0.4060134	total: 2m 10s	remaining: 32.4s
801:	learn: 0.4059281	total: 2m 10s	remaining: 32.3s
802:	learn: 0.4058069	total: 2m 10s	remaining: 32.1s
803:	learn: 0.4057491	total: 2m 11s	remaining: 31.9s
804:	lea

943:	learn: 0.3937565	total: 2m 29s	remaining: 8.88s
944:	learn: 0.3936946	total: 2m 29s	remaining: 8.72s
945:	learn: 0.3936315	total: 2m 29s	remaining: 8.56s
946:	learn: 0.3935687	total: 2m 30s	remaining: 8.4s
947:	learn: 0.3934931	total: 2m 30s	remaining: 8.23s
948:	learn: 0.3934428	total: 2m 30s	remaining: 8.07s
949:	learn: 0.3933933	total: 2m 30s	remaining: 7.91s
950:	learn: 0.3933019	total: 2m 30s	remaining: 7.75s
951:	learn: 0.3932474	total: 2m 30s	remaining: 7.59s
952:	learn: 0.3931673	total: 2m 30s	remaining: 7.43s
953:	learn: 0.3930880	total: 2m 30s	remaining: 7.26s
954:	learn: 0.3930119	total: 2m 30s	remaining: 7.1s
955:	learn: 0.3929465	total: 2m 30s	remaining: 6.94s
956:	learn: 0.3928751	total: 2m 30s	remaining: 6.78s
957:	learn: 0.3928145	total: 2m 31s	remaining: 6.62s
958:	learn: 0.3927458	total: 2m 31s	remaining: 6.46s
959:	learn: 0.3926187	total: 2m 31s	remaining: 6.3s
960:	learn: 0.3925345	total: 2m 31s	remaining: 6.14s
961:	learn: 0.3924463	total: 2m 31s	remaining: 5.

RandomizedSearchCV(cv=5,
                   estimator=Pipeline(steps=[('functiontransformer',
                                              FunctionTransformer(func=<function _encode_dates at 0x7fa59999fe50>)),
                                             ('columntransformer',
                                              ColumnTransformer(transformers=[('date',
                                                                               OneHotEncoder(handle_unknown='ignore'),
                                                                               ['year',
                                                                                'month',
                                                                                'day',
                                                                                'weekday',
                                                                                'hour']),
                                                                       

In [14]:
bestparams = rscv.best_params_
bestparams

{'catboostregressor__random_strength': 3,
 'catboostregressor__max_depth': 8,
 'catboostregressor__learning_rate': 0.1,
 'catboostregressor__l2_leaf_reg': 7,
 'catboostregressor__iterations': 1000,
 'catboostregressor__bagging_temperature': 0.3}

In [15]:
import joblib
joblib.dump(pipe, 'CATBoost')
joblib.dump(bestparams, 'CatB_Best_Model')

['CatB_Best_Model']

In [16]:
joblib.load('CatB_Best_Model')

{'catboostregressor__random_strength': 3,
 'catboostregressor__max_depth': 8,
 'catboostregressor__learning_rate': 0.1,
 'catboostregressor__l2_leaf_reg': 7,
 'catboostregressor__iterations': 1000,
 'catboostregressor__bagging_temperature': 0.3}

In [18]:
from sklearn.metrics import mean_squared_error, r2_score

print(
    f"Train set, RMSE={mean_squared_error(y_train, rscv.predict(X_train), squared=False):.7f}"
)
print(
    f"Test set, RMSE={mean_squared_error(y_test, rscv.predict(X_test), squared=False):.7f}"
)

print(
    f"Train set r2, RMSE={r2_score(y_train, rscv.predict(X_train)):.7f}"
)
print(
    f"Test set r2, RMSE={r2_score(y_test, rscv.predict(X_test)):.7f}"
)

Train set, RMSE=0.3899205
Test set, RMSE=0.4448188
Train set r2, RMSE=0.9458210
Test set r2, RMSE=0.9044587
